In [1]:
!pip install pettingzoo[classic]==1.22.3
!pip install Pillow
!pip install ray[rllib]
!pip install SuperSuit
!pip install torch
!pip install tensorflow-probability

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 816.1/816.1 kB 9.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 953.9/953.9 kB 42.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.1/147.1 kB 14.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 251.1/251.1 kB 22.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.7/13.7 MB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.5/115.5 kB 12.7 MB/s eta 0:00:00
  Created wheel for rlcard: filename=rlcard-1.0.5-py3-none-any.whl size=307097 sha256=c00c5ed96d568bab25c59e201683f271a955b9768fb1fc1cf80806ceb7e70d19
  Stored in directory: /root/.cache/pip/wheels/22/1b/a9/cb9a2009aefc3e311979e3764bc8e095cc6a2541fdc3ce1f60
Successfully built rlcard
  Attempting uninstall: pygame
    Found existing installation: pygame 2.5.1
    Uninstalling pygame-2.5.1:
      Successfully uninstalled pygame-2.5.1
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
!unzip '/content/colab_checkpoint_4.2Mil.zip'

Archive:  /content/colab_checkpoint_4.2Mil.zip
   creating: colab_checkpoint_4.2Mil/
   creating: colab_checkpoint_4.2Mil/checkpoint_004100/
 extracting: colab_checkpoint_4.2Mil/checkpoint_004100/.is_checkpoint  
  inflating: colab_checkpoint_4.2Mil/checkpoint_004100/.tune_metadata  
  inflating: colab_checkpoint_4.2Mil/checkpoint_004100/algorithm_state.pkl  
   creating: colab_checkpoint_4.2Mil/checkpoint_004100/policies/
   creating: colab_checkpoint_4.2Mil/checkpoint_004100/policies/player_0/
  inflating: colab_checkpoint_4.2Mil/checkpoint_004100/policies/player_0/policy_state.pkl  
  inflating: colab_checkpoint_4.2Mil/checkpoint_004100/policies/player_0/rllib_checkpoint.json  
   creating: colab_checkpoint_4.2Mil/checkpoint_004100/policies/player_1/
  inflating: colab_checkpoint_4.2Mil/checkpoint_004100/policies/player_1/policy_state.pkl  
  inflating: colab_checkpoint_4.2Mil/checkpoint_004100/policies/player_1/rllib_checkpoint.json  
  inflating: colab_checkpoint_4.2Mil/checkpoint

In [3]:
import os
import ray
import gymnasium as gym
from gym.spaces import Box, Discrete
from ray import tune
from ray.rllib.utils.framework import try_import_torch
from ray.rllib.models.torch.fcnet import FullyConnectedNetwork as TorchFC
from ray.rllib.models import ModelCatalog
from ray.rllib.algorithms.dqn.dqn_torch_model import DQNTorchModel
from ray.rllib.env import PettingZooEnv
from ray.rllib.algorithms.dqn import DQNConfig
from ray.rllib.utils.torch_utils import FLOAT_MAX
from ray.tune.registry import register_env
from ray import air
from pettingzoo.classic import hanabi_v4

torch, nn = try_import_torch()


# Adapted from [1], https://github.com/ray-project/ray/blob/master/rllib/examples/models/action_mask_model.py

class TorchMaskedActions(DQNTorchModel):
    """PyTorch version of above ParametricActionsModel."""

    def __init__(
        self,
        obs_space: Box,
        action_space: Discrete,
        num_outputs,
        model_config,
        name,
        **kw,
    ):
        DQNTorchModel.__init__(
            self, obs_space, action_space, num_outputs, model_config, name, **kw
        )

        obs_len = obs_space.shape[0] - action_space.n

        orig_obs_space = Box(
            shape=(obs_len,), low=obs_space.low[:obs_len], high=obs_space.high[:obs_len]
        )
        self.action_embed_model = TorchFC(
            orig_obs_space,
            action_space,
            action_space.n,
            model_config,
            name + "_action_embed",
        )

    def forward(self, input_dict, state, seq_lens):
        # Extract the available actions tensor from the observation.
        action_mask = input_dict["obs"]["action_mask"]

        # Compute the predicted action embedding
        action_logits, _ = self.action_embed_model(
            {"obs": input_dict["obs"]["observation"]}
        )
        # turns probit action mask into logit action mask to mask out invalid actions
        inf_mask = torch.clamp(torch.log(action_mask), -1e10, FLOAT_MAX)
        # print('info mask', inf_mask)
        # print('action logits', action_logits)
        return action_logits + inf_mask, state

    def value_function(self):
        return self.action_embed_model.value_function()

# Adapted from [2], https://github.com/Farama-Foundation/PettingZoo/blob/master/tutorials/Ray/rllib_leduc_holdem.py

if __name__ == "__main__":
    ray.shutdown()
    ray.init(num_cpus = 1, log_to_driver=False)

    alg_name = "DQN"
    # register environment with ray
    ModelCatalog.register_custom_model("pa_model", TorchMaskedActions)

    # create environment
    def env_creator():
        env = hanabi_v4.env(colors=2, ranks=5, players=2, hand_size=2, max_information_tokens=3, max_life_tokens=1)
        return env

    env_name = "hanabi_v4"
    # register environment with Ray
    register_env(env_name, lambda config: PettingZooEnv(env_creator()))

    # create instance of environment
    test_env = PettingZooEnv(env_creator())
    # get observation space
    obs_space = test_env.observation_space
    # get action space
    act_space = test_env.action_space

    # set configuration of DQN algorithm
    config = (
        DQNConfig() # calls DQN config class where DQN algo can be built
        .environment(env=env_name)
        # set rollouts
        .rollouts(num_rollout_workers=0, rollout_fragment_length=30)
        # set training configuration
        .training(
            train_batch_size=512,
            model={"custom_model": "pa_model", "fcnet_hiddens": [512, 512], 'fcnet_activation': 'relu'},
            replay_buffer_config = {"capacity": 1000000 },  # set replay buffer size
        )
        .debugging(
            log_level="DEBUG"
        )
        # set seperate policies for each agent
        .multi_agent(
            policies={
                "player_0": (None, obs_space, act_space, {}),
                "player_1": (None, obs_space, act_space, {}),
            },
            policy_mapping_fn=(lambda agent_id, *args, **kwargs: agent_id), # map policies to each player
        )
        # pytorch framework
        .framework(framework="torch")
        .exploration(
            exploration_config={
                "type": "EpsilonGreedy", # type of exploration
                "initial_epsilon": 0.000025, # initial epsilon value
                "final_epsilon": 0.0,       # final epsilon value
                "epsilon_timesteps": 1000,  # Timesteps over which to anneal epsilon.
            }
        )
        # allocate gpu resources
        .resources(num_gpus= 0)
    )

    # restore from checkpoint and run
    tune.run(
        alg_name,
        name="DQN",
        restore = '/content/colab_checkpoint_4.2Mil/checkpoint_004100', # resore path
        stop={"timesteps_total": 1000000}, # stop after 100 Mil timesteps
        checkpoint_freq=10, # checkpoint frequency
        config=config.to_dict(),
    )


/usr/local/lib/python3.10/dist-packages/tensorflow_probability/python/__init__.py:57: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if (distutils.version.LooseVersion(tf.__version__) <
2023-09-06 13:57:04,841	WARNING deprecation.py:50 -- DeprecationWarning: `DirectStepOptimizer` has been deprecated. This will raise an error in the future!
/usr/local/lib/python3.10/dist-packages/google/rpc/__init__.py:20: DeprecationWarning: Deprecated call to `pkg_resources.declare_namespace('google.rpc')`.
Implementing implicit namespace packages (as specified in PEP 420) is preferred to `pkg_resources.declare_namespace`. See https://setuptools.pypa.io/en/latest/references/keywords.html#keyword-namespace-packages
  pkg_resources.declare_namespace(__name__)
/usr/local/lib/python3.10/dist-packages/pkg_resources/__init__.py:2349: DeprecationWarning: Deprecated call to `pkg_resources.declare_namespace('google')`.
Implementing implicit namespace packages (as

+--------------------------------------------------------+
| Configuration for experiment     DQN                   |
+--------------------------------------------------------+
| Search algorithm                 BasicVariantGenerator |
| Scheduler                        FIFOScheduler         |
| Number of trials                 1                     |
+--------------------------------------------------------+

View detailed results here: /root/ray_results/DQN
To visualize your results with TensorBoard, run: `tensorboard --logdir /root/ray_results/DQN`

Trial status: 1 PENDING
Current time: 2023-09-06 13:57:13. Total running time: 0s
Logical resource usage: 0/1 CPUs, 0/0 GPUs
+--------------------------------------+
| Trial name                  status   |
+--------------------------------------+
| DQN_hanabi_v4_47ca5_00000   PENDING  |
+--------------------------------------+

Training started with configuration:
+------------------------------------------------------------------------

In [4]:
# !zip -r /root/ray_results/files2.zip /root/ray_results/DQN/DQN_hanabi_v4_35ff1_00000_0_2023-08-17_20-25-30

# from google.colab import files
# files.download("/root/ray_results/files2.zip")

In [5]:
final_results = [] # empty list

In [ ]:
import argparse
import os
import numpy as np
import ray
from ray.rllib.algorithms.algorithm import Algorithm
from ray.rllib.env.wrappers.pettingzoo_env import PettingZooEnv
from ray.rllib.models import ModelCatalog
from ray.tune.registry import register_env
from pettingzoo.classic import hanabi_v4
from ray.rllib.algorithms.alpha_zero.mcts import Node, RootParentNode
from ray.rllib.algorithms.alpha_zero.mcts import MCTS
os.environ["SDL_VIDEODRIVER"] = "dummy"

ray.shutdown()
ray.init()

alg_name = "DQN"

# register model with ray
ModelCatalog.register_custom_model("pa_model", TorchMaskedActions)

# environment creater function
def env_creator():
    env = hanabi_v4.env(colors=2, ranks=5, players=2, hand_size=2, max_information_tokens=3, max_life_tokens=1)
    return env

# create instance of environment
env = env_creator()
env_name = "hanabi_v4"
# register environment with ray
register_env(env_name, lambda config: PettingZooEnv(env_creator()))

# load saved checkpoint data
DQNAgent = Algorithm.from_checkpoint('/content/colab_checkpoint_4.2Mil/checkpoint_004100')

# reward dictionary for each agent
reward_sums = {a: 0 for a in env.possible_agents}
episode = 0
# reset the environment
env.reset()
# Iterate over each game
for episodes in range(50000):
  print(episodes)
  epsiode_result_list = []
  env.reset()
  game_turn = 0 # set game turn in episode to 0
  flag = False
  reward_sums = {a: 0 for a in env.possible_agents} # reward dictionary for each agent
  for agent in env.agent_iter(): # for each agent in environment
      observation, reward, termination, truncation, info = env.last() # get state
      obs = observation["observation"] # get observation
      reward_sums[agent] += reward # increase reward based on actions
      if termination or truncation: # if terminate episode
          action = None # set action to none
      else:
          policy = DQNAgent.get_policy(agent) # get policy of current agent
          # batch the observation and action mask
          batch_agent_obs = {
              "obs": {
                  "observation": np.expand_dims(observation["observation"], 0),
                  "action_mask": np.expand_dims(observation["action_mask"], 0),
              }
          }
          # compute actions of agent based upon policy of agent
          batched_output_action, state_out, info = policy.compute_actions_from_input_dict(
              batch_agent_obs
          )
          # get single action
          single_action = batched_output_action[0]
          action = single_action
      env.step(action) # environment step
      final_results.append(np.array([agent, game_turn, obs, reward, observation["action_mask"], action])) # append results to list
      if termination or truncation:
          if flag == True: # if flag is true print final epsiode information
            print('total_game_turns :', game_turn)
            print("reward_final :", reward_sums)
            game_turn = 0
          flag = True
      game_turn += 1
      env.render() # render the environment


2023-08-20 09:57:45,023	INFO worker.py:1621 -- Started a local Ray instance.
2023-08-20 09:57:47,706	WARNING algorithm_config.py:656 -- Cannot create DQNConfig from given `config_dict`! Property __stdout_file__ not supported.
2023-08-20 09:57:47,721	WARNING deprecation.py:50 -- DeprecationWarning: `rllib/algorithms/simple_q/` has been deprecated. Use `rllib_contrib/simple_q/` instead. This will raise an error in the future!
/usr/local/lib/python3.10/dist-packages/ray/rllib/algorithms/algorithm.py:484: RayDeprecationWarning: This API is deprecated and may be removed in future Ray releases. You could suppress this warning by setting env variable PYTHONWARNINGS="ignore::DeprecationWarning"
`UnifiedLogger` will be removed in Ray 2.7.
  return UnifiedLogger(config, logdir, loggers=None)
/usr/local/lib/python3.10/dist-packages/ray/tune/logger/unified.py:53: RayDeprecationWarning: This API is deprecated and may be removed in future Ray releases. You could suppress this warning by setting env 

0
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
1
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
2
total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
3
total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
4
total_game_turns : 33
reward_final : {'player_0': 4, 'player_1': 4}
5
total_game_turns : 34
reward_final : {'player_0': 3, 'player_1': 3}
6
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
7
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
8
total_game_turns : 30
reward_final : {'player_0': 6, 'player_1': 6}
9
total_game_turns : 33
reward_final : {'player_0': 4, 'player_1': 4}
10
total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
11
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
12
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
13
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
14
total_game_tu

2023-08-20 09:58:48,071	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.TorchDistributionWrapper` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!
2023-08-20 09:58:48,079	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.get_torch_categorical_class_with_temperature` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!


total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
743
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
744
total_game_turns : 33
reward_final : {'player_0': 4, 'player_1': 4}
745
total_game_turns : 32
reward_final : {'player_0': 4, 'player_1': 4}
746
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
747
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
748
total_game_turns : 32
reward_final : {'player_0': 6, 'player_1': 6}
749
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
750
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
751
total_game_turns : 31
reward_final : {'player_0': 5, 'player_1': 5}
752
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
753
total_game_turns : 33
reward_final : {'player_0': 4, 'player_1': 4}
754
total_game_turns : 31
reward_final : {'player_0': 5, 'player_1': 5}
755
total_game_turns : 33
reward_final : {'player_0': 4, 'player_1':

2023-08-20 09:59:48,079	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.TorchDistributionWrapper` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!
2023-08-20 09:59:48,083	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.get_torch_categorical_class_with_temperature` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!


...

total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
48311
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
48312
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
48313
total_game_turns : 31
reward_final : {'player_0': 5, 'player_1': 5}
48314
total_game_turns : 32
reward_final : {'player_0': 6, 'player_1': 6}
48315
total_game_turns : 12
reward_final : {'player_0': 0, 'player_1': 0}
48316
total_game_turns : 30
reward_final : {'player_0': 6, 'player_1': 6}
48317
total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
48318
total_game_turns : 30
reward_final : {'player_0': 6, 'player_1': 6}
48319
total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
48320
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
48321
total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
48322
total_game_turns : 31
reward_final : {'player_0': 5, 'player_1': 5}
48323
total_game_turns : 33
reward_final : {

2023-08-20 10:57:48,500	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.TorchDistributionWrapper` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!
2023-08-20 10:57:48,504	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.get_torch_categorical_class_with_temperature` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!


total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49084
total_game_turns : 33
reward_final : {'player_0': 6, 'player_1': 6}
49085
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49086
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
49087
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49088
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
49089
total_game_turns : 32
reward_final : {'player_0': 5, 'player_1': 5}
49090
total_game_turns : 29
reward_final : {'player_0': 6, 'player_1': 6}
49091
total_game_turns : 32
reward_final : {'player_0': 6, 'player_1': 6}
49092
total_game_turns : 32
reward_final : {'player_0': 6, 'player_1': 6}
49093
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49094
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49095
total_game_turns : 31
reward_final : {'player_0': 5, 'player_1': 5}
49096
total_game_turns : 31
reward_final : {

2023-08-20 10:58:48,506	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.TorchDistributionWrapper` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!
2023-08-20 10:58:48,510	WARNING deprecation.py:50 -- DeprecationWarning: `ray.rllib.models.torch.torch_action_dist.get_torch_categorical_class_with_temperature` has been deprecated. Use `ray.rllib.models.torch.torch_distributions.TorchCategorical` instead. This will raise an error in the future!


total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49885
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49886
total_game_turns : 33
reward_final : {'player_0': 6, 'player_1': 6}
49887
total_game_turns : 21
reward_final : {'player_0': 0, 'player_1': 0}
49888
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49889
total_game_turns : 31
reward_final : {'player_0': 6, 'player_1': 6}
49890
total_game_turns : 33
reward_final : {'player_0': 6, 'player_1': 6}
49891
total_game_turns : 33
reward_final : {'player_0': 4, 'player_1': 4}
49892
total_game_turns : 32
reward_final : {'player_0': 6, 'player_1': 6}
49893
total_game_turns : 31
reward_final : {'player_0': 5, 'player_1': 5}
49894
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49895
total_game_turns : 33
reward_final : {'player_0': 5, 'player_1': 5}
49896
total_game_turns : 31
reward_final : {'player_0': 0, 'player_1': 0}
49897
total_game_turns : 33
reward_final : {

In [ ]:
final_results = np.array(final_results) # convert to array

In [ ]:
import pandas as pd
df = pd.DataFrame(final_results) # convert to dataframe

In [ ]:
len(final_results) # get length of array

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


50072

In [ ]:
df.to_pickle('/content/dataset.pkl') # convert dataframe to pickle file

In [ ]:
from google.colab import files
files.download('dataset.pkl')

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# References

[1] “ray/rllib/examples/models/action_mask_model.py at master · ray-project/ray,” GitHub. https://github.com/ray-project/ray/blob/master/rllib/examples/models/action_mask_model.py (accessed Sep. 07, 2023).
 

[2] “PettingZoo/tutorials/Ray/rllib_leduc_holdem.py at master · Farama-Foundation/PettingZoo,” GitHub. https://github.com/Farama-Foundation/PettingZoo/blob/master/tutorials/Ray/rllib_leduc_holdem.py (accessed Sep. 07, 2023).
